<a href="https://colab.research.google.com/github/LauraMartinus/ukuxhumana/blob/master/fairseq/comparing_decomposers/nso_bpe_vs_morfessor.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

## Pytorch

In [1]:
# http://pytorch.org/
from os.path import exists
from wheel.pep425tags import get_abbr_impl, get_impl_ver, get_abi_tag
platform = '{}{}-{}'.format(get_abbr_impl(), get_impl_ver(), get_abi_tag())
cuda_output = !ldconfig -p|grep cudart.so|sed -e 's/.*\.\([0-9]*\)\.\([0-9]*\)$/cu\1\2/'
accelerator = cuda_output[0] if exists('/dev/nvidia0') else 'cpu'

!pip install -q http://download.pytorch.org/whl/{accelerator}/torch-0.4.1-{platform}-linux_x86_64.whl torchvision
import torch

tcmalloc: large alloc 1073750016 bytes == 0x5930e000 @  0x7f11e54502a4 0x591a07 0x5b5d56 0x502e9a 0x506859 0x502209 0x502f3d 0x506859 0x504c28 0x502540 0x502f3d 0x506859 0x504c28 0x502540 0x502f3d 0x506859 0x504c28 0x502540 0x502f3d 0x507641 0x502209 0x502f3d 0x506859 0x504c28 0x502540 0x502f3d 0x507641 0x504c28 0x502540 0x502f3d 0x507641


## Fairseq


In [2]:
!git clone https://github.com/pytorch/fairseq.git
import os
os.chdir("fairseq/")
!pip install -r requirements.txt
%run -i 'setup.py' build develop

Cloning into 'fairseq'...
remote: Enumerating objects: 48, done.
remote: Counting objects: 100% (48/48), done.
remote: Compressing objects: 100% (37/37), done.
remote: Total 3000 (delta 16), reused 21 (delta 11), pack-reused 2952
Receiving objects: 100% (3000/3000), 3.08 MiB | 3.25 MiB/s, done.
Resolving deltas: 100% (2175/2175), done.
    100% |████████████████████████████████| 430kB 7.9MB/s 
    100% |████████████████████████████████| 163kB 17.4MB/s 
  Running setup.py bdist_wheel for pycparser ... - \ done
  Stored in directory: /root/.cache/pip/wheels/f2/9a/90/de94f8556265ddc9d9c8b271b0f63e57b26fb1d67a45564511
Successfully built pycparser
running build
running build_py
creating build
creating build/lib.linux-x86_64-3.6
creating build/lib.linux-x86_64-3.6/tests
copying tests/test_dictionary.py -> build/lib.linux-x86_64-3.6/tests
copying tests/test_backtranslation_dataset.py -> build/lib.linux-x86_64-3.6/tests
copying tests/test_sequence_scorer.py -> build/lib.linux-x86_64-3.6/te

## Subword

In [0]:
!git clone https://github.com/rsennrich/subword-nmt

Cloning into 'subword-nmt'...
remote: Enumerating objects: 481, done.
remote: Total 481 (delta 0), reused 0 (delta 0), pack-reused 481
Receiving objects: 100% (481/481), 203.75 KiB | 2.91 MiB/s, done.
Resolving deltas: 100% (287/287), done.


## BPE

In [0]:
os.chdir('../')
!cat ennso_parallel.train.en ennso_parallel.train.nso > combine.txt

!fairseq/subword-nmt/learn_bpe.py -s 8000 <combine.txt> ennso.codes
!fairseq/subword-nmt/apply_bpe.py -c ennso.codes < ennso_parallel.train.en > train.en
!fairseq/subword-nmt/apply_bpe.py -c ennso.codes < ennso_parallel.train.nso > train.nso
!fairseq/subword-nmt/apply_bpe.py -c ennso.codes < ennso_parallel.dev.en > valid.en
!fairseq/subword-nmt/apply_bpe.py -c ennso.codes < ennso_parallel.dev.nso > valid.nso
!fairseq/subword-nmt/apply_bpe.py -c ennso.codes < ennso_parallel.test.en > test.en
!fairseq/subword-nmt/apply_bpe.py -c ennso.codes < ennso_parallel.test.nso > test.nso

os.chdir('fairseq/')
TEXT=".."
%run 'preprocess.py' --source-lang nso --target-lang en --trainpref $TEXT/train --validpref $TEXT/valid --testpref $TEXT/test --destdir data-bin/ennso

!mkdir -p checkpoint/fconv
!python train.py data-bin/ennso \
    --lr 0.25 --clip-norm 0.1 --dropout 0.2 --max-tokens 2000 \
    --arch fconv --save-dir checkpoint/fconv

# for sentencepiece remove ▁
output = %run 'generate.py' data-bin/ennso --path checkpoint/fconv/checkpoint_best.pt --beam 5 --batch-size 128 --remove-bpe --source-lang nso --target-lang en

fairseq/subword-nmt/learn_bpe.py:267: DeprecationWarning: this script's location has moved to /content/fairseq/subword-nmt/subword_nmt. This symbolic link will be removed in a future version. Please point to the new location, or install the package and use the command 'subword-nmt'
  DeprecationWarning
fairseq/subword-nmt/apply_bpe.py:334: DeprecationWarning: this script's location has moved to /content/fairseq/subword-nmt/subword_nmt. This symbolic link will be removed in a future version. Please point to the new location, or install the package and use the command 'subword-nmt'
  DeprecationWarning
fairseq/subword-nmt/apply_bpe.py:351: ResourceWarning: unclosed file <_io.TextIOWrapper name='ennso.codes' mode='r' encoding='UTF-8'>
  args.codes = codecs.open(args.codes.name, encoding='utf-8')
fairseq/subword-nmt/apply_bpe.py:334: DeprecationWarning: this script's location has moved to /content/fairseq/subword-nmt/subword_nmt. This symbolic link will be removed in a future version. Plea

## Morfessor

In [3]:
##NEED TO CHANGE FILE NAMES
TEXT=".."
%run 'preprocess.py' --source-lang nso --target-lang en --trainpref $TEXT/ennso_parallel.train.decomp --validpref $TEXT/ennso_parallel.dev.decomp --testpref $TEXT/ennso_parallel.test.decomp --destdir data-bin/de_ennso

!mkdir -p checkpoint/fconv
!python train.py data-bin/de_ennso \
    --lr 0.25 --clip-norm 0.1 --dropout 0.2 --max-tokens 500 \
    --arch fconv --save-dir chcpoint/fconv

# for sentencepiece remove ▁
output = %run 'generate.py' data-bin/de_ennso --path chcpoint/fconv/checkpoint_best.pt --beam 5 --batch-size 128 --remove-bpe --source-lang nso --target-lang en

Namespace(alignfile=None, destdir='data-bin/de_ennso', joined_dictionary=False, nwordssrc=-1, nwordstgt=-1, only_source=False, output_format='binary', padding_factor=8, source_lang='nso', srcdict=None, target_lang='en', testpref='../ennso_parallel.test.decomp', tgtdict=None, thresholdsrc=0, thresholdtgt=0, trainpref='../ennso_parallel.train.decomp', validpref='../ennso_parallel.dev.decomp', workers=1)
| [nso] Dictionary: 9711 types
| [nso] ../ennso_parallel.train.decomp.nso: 21543 sents, 652867 tokens, 0.0% replaced by <unk>
| [nso] Dictionary: 9711 types
| [nso] ../ennso_parallel.dev.decomp.nso: 6234 sents, 191574 tokens, 0.00679% replaced by <unk>
| [nso] Dictionary: 9711 types
| [nso] ../ennso_parallel.test.decomp.nso: 3000 sents, 72070 tokens, 0.0139% replaced by <unk>
| [en] Dictionary: 41743 types
| [en] ../ennso_parallel.train.decomp.en: 21543 sents, 390176 tokens, 0.0% replaced by <unk>
| [en] Dictionary: 41743 types
| [en] ../ennso_parallel.dev.decomp.en: 6234 sents, 124287 to

## BPE Eng Morfessor NSO

In [0]:
os.chdir('../')
#!cat enzu_parallel.train.en enzu_parallel.train.zu > combine.txt

!fairseq/subword-nmt/learn_bpe.py -s 8000 <ennso_parallel.train.en> ennso.codes
!fairseq/subword-nmt/apply_bpe.py -c ennso.codes < ennso_parallel.train.en > ennso_parallel.train.decomp.en
#!fairseq/subword-nmt/apply_bpe.py -c enzu.codes < enzu_parallel.train.zu > train.zu
!fairseq/subword-nmt/apply_bpe.py -c ennso.codes < ennso_parallel.dev.en > ennso_parallel.dev.decomp.en
#!fairseq/subword-nmt/apply_bpe.py -c enzu.codes < enzu_parallel.dev.zu > valid.zu
!fairseq/subword-nmt/apply_bpe.py -c ennso.codes < ennso_parallel.test.en > ennso_parallel.test.decomp.en
#!fairseq/subword-nmt/apply_bpe.py -c enzu.codes < enzu_parallel.test.zu > test.zu
os.chdir('fairseq/')

fairseq/subword-nmt/learn_bpe.py:267: DeprecationWarning: this script's location has moved to /content/fairseq/subword-nmt/subword_nmt. This symbolic link will be removed in a future version. Please point to the new location, or install the package and use the command 'subword-nmt'
  DeprecationWarning
fairseq/subword-nmt/apply_bpe.py:334: DeprecationWarning: this script's location has moved to /content/fairseq/subword-nmt/subword_nmt. This symbolic link will be removed in a future version. Please point to the new location, or install the package and use the command 'subword-nmt'
  DeprecationWarning
fairseq/subword-nmt/apply_bpe.py:351: ResourceWarning: unclosed file <_io.TextIOWrapper name='ennso.codes' mode='r' encoding='UTF-8'>
  args.codes = codecs.open(args.codes.name, encoding='utf-8')
fairseq/subword-nmt/apply_bpe.py:334: DeprecationWarning: this script's location has moved to /content/fairseq/subword-nmt/subword_nmt. This symbolic link will be removed in a future version. Plea

In [0]:
TEXT=".."
%run 'preprocess.py' --source-lang nso --target-lang en --trainpref $TEXT/ennso_parallel.train.decomp --validpref $TEXT/ennso_parallel.dev.decomp --testpref $TEXT/ennso_parallel.test.decomp --destdir data-bin/de_ennso

!mkdir -p checkpoint/fconv
!python train.py data-bin/de_ennso \
    --lr 0.25 --clip-norm 0.1 --dropout 0.2 --max-tokens 500 \
    --arch fconv --save-dir chkpoint/fconv

# for sentencepiece remove ▁
output = %run 'generate.py' data-bin/de_ennso --path chkpoint/fconv/checkpoint_best.pt --beam 5 --batch-size 128 --remove-bpe --source-lang nso --target-lang en

Namespace(alignfile=None, destdir='data-bin/de_ennso', joined_dictionary=False, nwordssrc=-1, nwordstgt=-1, only_source=False, output_format='binary', padding_factor=8, source_lang='nso', srcdict=None, target_lang='en', testpref='../ennso_parallel.test.decomp', tgtdict=None, thresholdsrc=0, thresholdtgt=0, trainpref='../ennso_parallel.train.decomp', validpref='../ennso_parallel.dev.decomp', workers=1)
| [nso] Dictionary: 9711 types
| [nso] ../ennso_parallel.train.decomp.nso: 21543 sents, 652867 tokens, 0.0% replaced by <unk>
| [nso] Dictionary: 9711 types
| [nso] ../ennso_parallel.dev.decomp.nso: 6234 sents, 191574 tokens, 0.00679% replaced by <unk>
| [nso] Dictionary: 9711 types
| [nso] ../ennso_parallel.test.decomp.nso: 3000 sents, 72070 tokens, 0.0139% replaced by <unk>
| [en] Dictionary: 8063 types
| [en] ../ennso_parallel.train.decomp.en: 21543 sents, 522248 tokens, 0.0% replaced by <unk>
| [en] Dictionary: 8063 types
| [en] ../ennso_parallel.dev.decomp.en: 6234 sents, 153329 toke

## Clean

In [0]:
TEXT=".."
%run 'preprocess.py' --source-lang nso --target-lang en --trainpref $TEXT/ennso_parallel.train --validpref $TEXT/ennso_parallel.dev --testpref $TEXT/ennso_parallel.test --destdir data-bin/de_ennso

!mkdir -p checkpoint/fconv
!python train.py data-bin/de_ennso \
    --lr 0.25 --clip-norm 0.1 --dropout 0.2 --max-tokens 2000 \
    --arch fconv --save-dir chckpoint/fconv

# for sentencepiece remove ▁
output = %run 'generate.py' data-bin/de_ennso --path chckpoint/fconv/checkpoint_best.pt --beam 5 --batch-size 128 --remove-bpe --source-lang nso --target-lang en

Namespace(alignfile=None, destdir='data-bin/de_ennso', joined_dictionary=False, nwordssrc=-1, nwordstgt=-1, only_source=False, output_format='binary', padding_factor=8, source_lang='nso', srcdict=None, target_lang='en', testpref='../ennso_parallel.test', tgtdict=None, thresholdsrc=0, thresholdtgt=0, trainpref='../ennso_parallel.train', validpref='../ennso_parallel.dev', workers=1)
| [nso] Dictionary: 38919 types
| [nso] ../ennso_parallel.train.nso: 21543 sents, 498913 tokens, 0.0% replaced by <unk>
| [nso] Dictionary: 38919 types
| [nso] ../ennso_parallel.dev.nso: 6234 sents, 149829 tokens, 4.45% replaced by <unk>
| [nso] Dictionary: 38919 types
| [nso] ../ennso_parallel.test.nso: 3000 sents, 55235 tokens, 3.89% replaced by <unk>
| [en] Dictionary: 41743 types
| [en] ../ennso_parallel.train.en: 21543 sents, 390176 tokens, 0.0% replaced by <unk>
| [en] Dictionary: 41743 types
| [en] ../ennso_parallel.dev.en: 6234 sents, 124287 tokens, 3.77% replaced by <unk>
| [en] Dictionary: 41743 typ

## Results

BPE 8k: 11.98

Morfessor: 2.46

BPE Eng Morfessor Nso: 0.5

Clean: 5.80